In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Acute_Myeloid_Leukemia"
cohort = "GSE98578"

# Input paths
in_trait_dir = "../../input/GEO/Acute_Myeloid_Leukemia"
in_cohort_dir = "../../input/GEO/Acute_Myeloid_Leukemia/GSE98578"

# Output paths
out_data_file = "../../output/preprocess/Acute_Myeloid_Leukemia/GSE98578.csv"
out_gene_data_file = "../../output/preprocess/Acute_Myeloid_Leukemia/gene_data/GSE98578.csv"
out_clinical_data_file = "../../output/preprocess/Acute_Myeloid_Leukemia/clinical_data/GSE98578.csv"
json_path = "../../output/preprocess/Acute_Myeloid_Leukemia/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Expression data from cultured human acute megokaryblastic myeloid leukemia and acute myeloid leukemia cell lines"
!Series_summary	"The genetic lesions that drive acute megakaryoblastic leukemia (AMKL) have not been fully elucidated. To search for AMKL gene, we subjected 9 AMKL cell lines and 39 non-AMKL acute myeloid leukemia cell lines to microarray gene expression analysis."
!Series_overall_design	"9 AMKL and 39 non-AMKL acute myeloid leukemia cell lines expression data"
Sample Characteristics Dictionary:
{0: ['cell line: CMK', 'cell line: ML-2', 'cell line: OCI-AML2', 'cell line: OCI-AML3', 'cell line: OCI-M1', 'cell line: OCI-M2', 'cell line: SKM-1', 'cell line: SIG-M5', 'cell line: PLB-985', 'cell line: MOLM-13', 'cell line: EOL-1', 'cell line: HNT-34', 'cell line: MG-S', 'cell line: U937', 'cell line: THP-1', 'cell line: KG-1', 'cell line: HL60/MX1', 'cell line: MOLM14', 'cell line: MV4;11', 'cell line: GDM-1', 'cell line: KU812', 'cell line

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
import pandas as pd
import os
import json
from typing import Optional, Callable, Dict, Any

# 1. Gene Expression Data Availability
# Based on the series title and design, this dataset contains gene expression data
is_gene_available = True

# 2. Variable Availability and Data Type Conversion
# 2.1 Data Availability
# From the sample characteristics dictionary, we can infer:
# - trait information is in row 2 (cell subtype: AMKL or non-AMKL)
# - age data is not available 
# - gender data is not available

trait_row = 2  # Cell subtype (AMKL or non-AMKL)
age_row = None  # Age information not available
gender_row = None  # Gender information not available

# 2.2 Data Type Conversion
def convert_trait(value):
    """Convert AML subtype to binary format.
    AMKL = 1, non-AMKL = 0
    """
    if value is None:
        return None
    
    if ':' in value:
        value = value.split(':', 1)[1].strip()
    
    if value.lower() == 'amkl':
        return 1
    elif value.lower() == 'non-amkl':
        return 0
    else:
        return None

def convert_age(value):
    """Convert age to float, but it's not used in this dataset."""
    return None

def convert_gender(value):
    """Convert gender to binary, but it's not used in this dataset."""
    return None

# 3. Save Metadata
# Determine if trait data is available
is_trait_available = trait_row is not None

# Conduct initial filtering and save metadata
validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
# Only execute if trait data is available
if trait_row is not None:
    # Load the clinical data from the previous step
    clinical_data_path = os.path.join(in_cohort_dir, "clinical_data.csv")
    if os.path.exists(clinical_data_path):
        clinical_data = pd.read_csv(clinical_data_path)
        
        # Extract clinical features
        selected_clinical_df = geo_select_clinical_features(
            clinical_df=clinical_data,
            trait=trait,
            trait_row=trait_row,
            convert_trait=convert_trait,
            age_row=age_row,
            convert_age=convert_age,
            gender_row=gender_row,
            convert_gender=convert_gender
        )
        
        # Preview the extracted clinical data
        preview = preview_df(selected_clinical_df)
        print("Clinical data preview:", preview)
        
        # Save the clinical data to CSV
        os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
        selected_clinical_df.to_csv(out_clinical_data_file, index=False)
        print(f"Clinical data saved to {out_clinical_data_file}")


### Step 3: Gene Data Extraction

In [4]:
# 1. Use the get_genetic_data function from the library to get the gene_data from the matrix_file previously defined.
gene_data = get_genetic_data(matrix_file)

# 2. Print the first 20 row IDs (gene or probe identifiers) for future observation.
print(gene_data.index[:20])


Index(['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at', '1294_at',
       '1316_at', '1320_at', '1405_i_at', '1431_at', '1438_at', '1487_at',
       '1494_f_at', '1552256_a_at', '1552257_a_at', '1552258_at', '1552261_at',
       '1552263_at', '1552264_a_at', '1552266_at'],
      dtype='object', name='ID')


### Step 4: Gene Identifier Review

In [5]:
# Examining the gene identifiers in the gene expression data
# These identifiers are in the format of probe IDs (e.g., '1007_s_at', '1053_at'), 
# which are Affymetrix probe identifiers rather than standard human gene symbols.
# Affymetrix IDs need to be mapped to official gene symbols for biological interpretation.

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 2. Use the 'preview_df' function from the library to preview the data and print out the results.
print("Gene annotation preview:")
print(preview_df(gene_annotation))


Gene annotation preview:
{'ID': ['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at'], 'GB_ACC': ['U48705', 'M87338', 'X51757', 'X69699', 'L36861'], 'SPOT_ID': [nan, nan, nan, nan, nan], 'Species Scientific Name': ['Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens'], 'Annotation Date': ['Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014'], 'Sequence Type': ['Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence'], 'Sequence Source': ['Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database'], 'Target Description': ['U48705 /FEATURE=mRNA /DEFINITION=HSU48705 Human receptor tyrosine kinase DDR gene, complete cds', 'M87338 /FEATURE= /DEFINITION=HUMA1SBU Human replication factor C, 40-kDa subunit (A1) mRNA, complete cds', "X51757 /FEATURE=cds /DEFINITION=HSP70B Human heat-shock protein HSP70B' gene", 'X69699 /FEATURE= /DEF

### Step 6: Gene Identifier Mapping

In [7]:
# 1. Based on the gene_annotation preview, we need to map the 'ID' column (probe identifiers) 
# to the 'Gene Symbol' column (human gene symbols)
prob_col = 'ID'  # Column containing the probe identifiers
gene_col = 'Gene Symbol'  # Column containing the gene symbols

# 2. Create a mapping dataframe using the 'get_gene_mapping' function from the library
gene_mapping = get_gene_mapping(gene_annotation, prob_col, gene_col)

# 3. Apply the gene mapping to convert probe-level measurements to gene expression data
gene_data = apply_gene_mapping(gene_data, gene_mapping)

# Print the number of genes after mapping and preview a few gene names
print(f"Number of genes after mapping: {len(gene_data)}")
print("First 20 gene symbols:")
print(gene_data.index[:20])


Number of genes after mapping: 21278
First 20 gene symbols:
Index(['A1BG', 'A1BG-AS1', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1', 'A2MP1',
       'A4GALT', 'A4GNT', 'AA06', 'AAAS', 'AACS', 'AACSP1', 'AADAC', 'AADACL2',
       'AADACP1', 'AADAT', 'AAED1', 'AAGAB', 'AAK1'],
      dtype='object', name='Gene')


### Step 7: Data Normalization and Linking

In [8]:
# 1. Normalize the obtained gene data with the 'normalize_gene_symbols_in_index' function from the library.
normalized_gene_data = normalize_gene_symbols_in_index(gene_data)
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
normalized_gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# Need to recreate the clinical data extraction since it wasn't successfully executed in Step 2
def convert_trait(value):
    """Convert AML subtype to binary format.
    AMKL = 1, non-AMKL = 0
    """
    if value is None:
        return None
    
    if ':' in value:
        value = value.split(':', 1)[1].strip()
    
    if value.lower() == 'amkl':
        return 1
    elif value.lower() == 'non-amkl':
        return 0
    else:
        return None

# Define the row indices for clinical features based on the sample characteristics dictionary inspection
trait_row = 2  # Cell subtype (AMKL or non-AMKL)
age_row = None  # Age information not available
gender_row = None  # Gender information not available

# Extract clinical features using the library function
selected_clinical_data = geo_select_clinical_features(
    clinical_df=clinical_data,
    trait=trait,
    trait_row=trait_row,
    convert_trait=convert_trait,
    age_row=age_row,
    convert_age=None,
    gender_row=gender_row,
    convert_gender=None
)

print("Clinical data preview:")
print(preview_df(selected_clinical_data))
os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
selected_clinical_data.to_csv(out_clinical_data_file)
print(f"Clinical data saved to {out_clinical_data_file}")

# 2. Link the clinical and genetic data with the 'geo_link_clinical_genetic_data' function from the library.
linked_data = geo_link_clinical_genetic_data(selected_clinical_data, normalized_gene_data)
print(f"Linked data shape: {linked_data.shape}")

# 3. Handle missing values in the linked data
linked_data = handle_missing_values(linked_data, trait)
print(f"Data shape after handling missing values: {linked_data.shape}")

# 4. Determine whether the trait and some demographic features are severely biased, and remove biased features.
is_trait_biased, unbiased_linked_data = judge_and_remove_biased_features(linked_data, trait)

# 5. Conduct quality check and save the cohort information.
is_usable = validate_and_save_cohort_info(
    is_final=True, 
    cohort=cohort, 
    info_path=json_path, 
    is_gene_available=True, 
    is_trait_available=True, 
    is_biased=is_trait_biased, 
    df=unbiased_linked_data,
    note="Dataset contains gene expression data from AMKL vs non-AMKL AML cell lines"
)

# 6. If the linked data is usable, save it as a CSV file to 'out_data_file'.
if is_usable:
    os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
    unbiased_linked_data.to_csv(out_data_file)
    print(f"Processed dataset saved to {out_data_file}")
else:
    print("Dataset not usable due to bias in trait distribution. Data not saved.")

Normalized gene data saved to ../../output/preprocess/Acute_Myeloid_Leukemia/gene_data/GSE98578.csv
Clinical data preview:
{'GSM2601197': [1.0], 'GSM2601198': [0.0], 'GSM2601199': [0.0], 'GSM2601200': [0.0], 'GSM2601201': [0.0], 'GSM2601202': [0.0], 'GSM2601203': [0.0], 'GSM2601204': [0.0], 'GSM2601205': [0.0], 'GSM2601206': [0.0], 'GSM2601207': [0.0], 'GSM2601208': [0.0], 'GSM2601209': [1.0], 'GSM2601210': [0.0], 'GSM2601211': [0.0], 'GSM2601212': [0.0], 'GSM2601213': [0.0], 'GSM2601214': [0.0], 'GSM2601215': [0.0], 'GSM2601216': [0.0], 'GSM2601217': [0.0], 'GSM2601218': [0.0], 'GSM2601219': [0.0], 'GSM2601220': [0.0], 'GSM2601221': [0.0], 'GSM2601222': [1.0], 'GSM2601223': [0.0], 'GSM2601224': [0.0], 'GSM2601225': [0.0], 'GSM2601226': [1.0], 'GSM2601227': [1.0], 'GSM2601228': [0.0], 'GSM2601229': [0.0], 'GSM2601230': [0.0], 'GSM2601231': [0.0], 'GSM2601232': [0.0], 'GSM2601233': [0.0], 'GSM2601234': [1.0], 'GSM2601235': [0.0], 'GSM2601236': [1.0], 'GSM2601237': [0.0], 'GSM2601238': [

Data shape after handling missing values: (48, 19846)
For the feature 'Acute_Myeloid_Leukemia', the least common label is '1.0' with 9 occurrences. This represents 18.75% of the dataset.
The distribution of the feature 'Acute_Myeloid_Leukemia' in this dataset is fine.



Processed dataset saved to ../../output/preprocess/Acute_Myeloid_Leukemia/GSE98578.csv
